In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [23]:
import pandas as pd
file_path_road = '/content/drive/My Drive/Xuancheng_data/road_data.csv'

df_roads = pd.read_csv(file_path_road)
df_roads.head()

cid  nlane     turn                                   dnroad  \
0  4393_4423      3    S#U#L            4423_4471#4423_4393#4423_4448   
1  4393_9052      0  L#S#U#R  9052_8367#9052_9051#9052_4393#9052_9135   
2  4423_4471      4  R#S#U#L  4471_4440#4471_4493#4471_4423#4471_4496   
3  4438_4439      0      S#U                      4439_4448#4439_4438   
4  4438_4474      2  R#S#U#L  4474_4448#4474_4582#4474_4438#4474_4502   

                                                geom          len  
0  LINESTRING(118.723892282 30.9160036330001;118....   612.797776  
1  LINESTRING(118.723892282 30.9160036330001;118....  1066.484653  
2  LINESTRING(118.728375699 30.9199501530001;118....   662.195967  
3  LINESTRING(118.718755032 30.9211743930001;118....   462.097261  
4  LINESTRING(118.718755032 30.9211743930001;118....   411.547206

In [24]:
file_path_veh1 = '/content/drive/My Drive/Xuancheng_data/veh1_data.csv'
df_veh1 = pd.read_csv(file_path_veh1)
df_veh1.head(5)

cid  type                 time         lon  \
0  b62b0f461be5ee9702131b83ac8a1abb     2  2020-09-01 10:23:50  118.762569   
1  b62b0f461be5ee9702131b83ac8a1abb     2  2020-09-01 10:24:00  118.762527   
2  b62b0f461be5ee9702131b83ac8a1abb     2  2020-09-01 10:24:10  118.762484   
3  b62b0f461be5ee9702131b83ac8a1abb     2  2020-09-01 10:24:20  118.762442   
4  b62b0f461be5ee9702131b83ac8a1abb     2  2020-09-01 10:24:30  118.762399   

         lat       spd     turn         dis     roadid  
0  30.943402  3.127881  Unknown  297.148700  4724_4664  
1  30.943123  3.127881  Unknown  265.869890  4724_4664  
2  30.942844  3.127881  Unknown  234.591079  4724_4664  
3  30.942565  3.127881  Unknown  203.312269  4724_4664  
4  30.942286  3.127881  Unknown  172.033458  4724_4664

In [25]:
df_veh1['time'] = pd.to_datetime(df_veh1['time'])
df_veh1 = df_veh1.sort_values(by='time')
df_veh1['time_diff'] = df_veh1['time'].diff().fillna(pd.Timedelta(seconds=0))
threshold = pd.Timedelta(minutes=10)
group_ids = (df_veh1['time_diff'] > threshold).cumsum()
grouped_veh1_data = [group for _, group in df_veh1.groupby(group_ids)]
for i, group in enumerate(grouped_veh1_data):
    print(f"Group {i + 1}:")
    print(group)
    print()

Group 1:
                                   cid  type                time         lon  \
2205  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:03:50  118.763317   
2206  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:04:00  118.763275   
2207  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:04:10  118.763228   
2208  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:04:20  118.763181   
2209  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:04:30  118.763134   
...                                ...   ...                 ...         ...   
1013  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:15:10  118.723577   
1014  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:15:20  118.722929   
1015  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:15:30  118.722276   
1016  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:15:40  118.721624   
1017  b62b0f461be5ee9702131b83ac8a1abb     2 2020-09-01 00:15:50  118.720971   

            lat       spd     

In [48]:
import pandas as pd
import folium
from folium.plugins import AntPath
from geopy.distance import geodesic
import matplotlib.colors as mcolors
import numpy as np
import networkx as nx
from shapely.geometry import shape
import json

# Fix the geom column: Replace semicolons with commas
df_roads['geom'] = df_roads['geom'].str.replace(';', ',')

# Build a road network graph
G = nx.Graph()

# Add edges to the graph based on road connections
for _, row in df_roads.iterrows():
    cid = row['cid']
    connected_roads = row['dnroad'].split('#')
    for connected_road in connected_roads:
        G.add_edge(cid, connected_road, weight=row['len'])

# Function to find the shortest path between two road segments
def find_shortest_path(graph, start, end):
    """Find the shortest path between two road segments using Dijkstra's algorithm."""
    try:
        return nx.shortest_path(graph, start, end, weight='weight')
    except nx.NetworkXNoPath:
        return None

# Function to parse LINESTRING into GeoJSON
def linestring_to_geojson(geom):
    """Convert a LINESTRING in WKT format to GeoJSON."""
    line = loads(geom)  # Parse WKT to Shapely geometry
    return json.loads(json.dumps(line.__geo_interface__))  # Convert to GeoJSON

# Function to connect unconnected road segments within a group
def connect_road_segments(group, graph):
    """Connect unconnected road segments within a group using the shortest path."""
    connected_segments = []
    for i in range(len(group) - 1):
        current_road = group.iloc[i]['roadid']
        next_road = group.iloc[i + 1]['roadid']

        # Check if the roads are connected
        if current_road.split('_')[1] != next_road.split('_')[0]:
            # Find the shortest path between the current road and the next road
            path = find_shortest_path(graph, current_road, next_road)
            if path:
                connected_segments.extend(path)
            else:
                print(f"No path found between {current_road} and {next_road}")
        else:
            connected_segments.append(current_road)

    # Add the last road segment
    connected_segments.append(group.iloc[-1]['roadid'])
    return connected_segments

# Create a color gradient for 23 groups
colors_list = ["red", "orange", "yellow", "lime", "green", "cyan", "blue", "indigo", "violet"]
cmap = mcolors.LinearSegmentedColormap.from_list("custom_gradient", colors_list)
colors = list(cmap(np.linspace(0, 1, 23)))

# Create a map centered on the first point of the first group
first_group = grouped_veh1_data[0]
midpoint = (first_group['lat'].mean(), first_group['lon'].mean())
m = folium.Map(location=midpoint, zoom_start=15)

# Plot each group with a gradient color
for i, group in enumerate(grouped_veh1_data):
    # Connect road segments within the group
    connected_segments = connect_road_segments(group, G)

    # Get the color for this group
    color = mcolors.to_hex(colors[i])

    # Plot each road segment in the group
    for segment in connected_segments:
        road = df_roads[df_roads['cid'] == segment]
        if not road.empty:
            geom = road['geom'].iloc[0]
            geojson = linestring_to_geojson(geom)

            # Add the road segment to the map using GeoJSON
            folium.GeoJson(
                geojson,
                style_function=lambda x, color=color: {'color': color, 'weight': 4}
            ).add_to(m)

    folium.CircleMarker(
        location=(group.iloc[0]['lat'], group.iloc[0]['lon']),
        radius=5,
        color=color,
        fill=True,
        popup=f"Group {i + 1} Start",
        tooltip=f"Group {i + 1} Start"
    ).add_to(m)

    folium.CircleMarker(
        location=(group.iloc[-1]['lat'], group.iloc[-1]['lon']),
        radius=5,
        color=color,
        fill=True,
        popup=f"Group {i + 1} End",
        tooltip=f"Group {i + 1} End"
    ).add_to(m)

# Display the map
m